In [99]:
import minsearch
import json
import os
import re 
from openai import OpenAI

In [61]:
base = os.getcwd()  # folder where Jupyter is running
path = os.path.join(base, "data", "stardew_all_combined.json")

with open(path, 'r', encoding='utf-8') as f:
    data = json.load(f)


In [62]:
data

{'pages': [{'title': "'1000 Years From Now'",
   'link': 'https://stardewvalleywiki.com/%271000_Years_From_Now%27',
   'sections': [{'section_title': 'main',
     'text': '\' 1000 Years From Now\' is a piece of furniture that hangs on a wall. It rotates into Famous Painter Lupini\'s stock on Winter 16 during the Night Market starting in year 2, and reappears on Winter 16 every 3 years. It can be purchased for data-sort-value="1200"> 1,200g .'}]},
  {'title': "'A Night On Eco-Hill'",
   'link': 'https://stardewvalleywiki.com/%27A_Night_On_Eco-Hill%27',
   'sections': [{'section_title': 'main',
     'text': '\' A Night On Eco-Hill\' is a piece of furniture that hangs on a wall. It can be obtained only by donating 20 items to the Museum .\nIf the original is lost, a replacement can be purchased at the Lost Items Shop in the Secret Woods for data-sort-value="10000"> 10,000g .'}]},
  {'title': "'Abstract'",
   'link': 'https://stardewvalleywiki.com/%27Abstract%27',
   'sections': [{'section

In [87]:
pages = []

for d in data["pages"]:
    text = ""
    for section in d["sections"]:
        # Clean section title
        section_title_clean = re.sub(r"[_\-']", ' ', section["section_title"]).strip()
        text += "section " + section_title_clean + "\n" + section["text"] + " "
    # Clean page title
    page_title_clean = re.sub(r"[_\-']", ' ', d["title"]).strip()
    pages.append({"link": d["link"], "title": page_title_clean, "text": text})

    

In [91]:
pages

[{'link': 'https://stardewvalleywiki.com/%271000_Years_From_Now%27',
  'title': '1000 Years From Now',
  'text': 'section main\n\' 1000 Years From Now\' is a piece of furniture that hangs on a wall. It rotates into Famous Painter Lupini\'s stock on Winter 16 during the Night Market starting in year 2, and reappears on Winter 16 every 3 years. It can be purchased for data-sort-value="1200"> 1,200g . '},
 {'link': 'https://stardewvalleywiki.com/%27A_Night_On_Eco-Hill%27',
  'title': 'A Night On Eco Hill',
  'text': 'section main\n\' A Night On Eco-Hill\' is a piece of furniture that hangs on a wall. It can be obtained only by donating 20 items to the Museum .\nIf the original is lost, a replacement can be purchased at the Lost Items Shop in the Secret Woods for data-sort-value="10000"> 10,000g . '},
 {'link': 'https://stardewvalleywiki.com/%27Abstract%27',
  'title': 'Abstract',
  'text': "section main\nThe ' Abstract' painting is a furniture item available from the Retro Catalogue . "},

In [92]:
index= minsearch.Index(
    text_fields=["title","sections"],
    keyword_fields=["link"]
)

In [93]:
index.fit(pages)

In [94]:
def search(query, top_k=3):
    boost = {"title": 2.0, "sections": 1.0}
    results = index.search(
        query, 
        boost_dict=boost,
        num_results=top_k
        )
    return results

In [110]:
def propmt_generation(query, search_results):
    prompot = """
    You are an virtual assistant for the game Stardew Valley.
    You will be provided with a question and some context from the Stardew Valley wiki.
    Use the context to answer the question as accurately as possible.
    Question: {query}
    Context: {context}
    """.strip()
    
    context = "\n".join([f"{i+1}. {res['title']}: {res['text']}" for i, res in enumerate(search_results)])
    return prompot.format(query=query, context=context)

In [100]:
client = OpenAI()

In [104]:
response = client.chat.completions.create(
    model='gpt-5-mini',
    messages=[{"role": "user", "content": "what is RAG?"}],
)

response.choices[0].message.content

'Most likely you mean Retrieval‑Augmented Generation (RAG). Briefly:\n\nWhat RAG is\n- RAG is an approach that combines a retrieval system (search over external documents) with a generative model (an LLM) so the model generates answers grounded in retrieved source text instead of relying only on its parametric memory.\n\nHow it works (high level)\n1. Index: convert documents into a searchable form (usually embeddings stored in a vector database).\n2. Retrieve: for a user query, find the top‑k most relevant documents/snippets (dense or sparse retrieval).\n3. Augment prompt: include the retrieved text (or summaries) in the prompt/context for the generator.\n4. Generate: the LLM composes the final answer using the retrieved context (and can cite sources if desired).\n\nVariants\n- RAG-Sequence vs RAG-Token (from the original Facebook/Meta RAG paper): differ in how retrieved documents are combined when computing the answer.\n- Retrieval + reranker: use a reranker to improve retrieval quali

In [105]:
def llm(prompt):
    response = client.chat.completions.create(
        model='gpt-5-mini',
        messages=[{"role": "user", "content": prompt}]
    )
    
    return response.choices[0].message.content



In [106]:
def RAG(query, top_k=3):
    search_results = search(query, top_k=top_k)
    prompt = propmt_generation(query, search_results)
    answer = llm(prompt)
    return answer, search_results


In [111]:
search_results = search("How to raise friendship with Abigail?", top_k=3)
search_results

[{'link': 'https://stardewvalleywiki.com/Abby',
  'title': 'Abigail',
  'text': 'section main\nPierre (Father)\nCaroline (Mother)\nAbigail is a villager who lives at Pierre\'s General Store in Pelican Town . She\'s one of the twelve characters available to marry . section Schedule\nAfter the Beach Resort on Ginger Island is unlocked, Abigail may randomly spend the day there. After leaving the Island at 6pm, Abigail will immediately go home to bed. Abigail never visits the Resort on Festival days or her checkup day at Harvey\'s Clinic .\nShown below are Abigail\'s schedules prioritized highest to lowest within each season. For example, if it is raining, that schedule overrides all others below it.\nSpring 4\nSpring 15 (Bus Service Restored)\nDesert Festival (As Vendor)\nSpring 6 and 16\nSpring 11 and 25 (No player has 6 hearts with Sebastian or Abigail)\nSpring 11 and 25\nRain (Option 1)\nRain (Option 2)\nWednesday\nFriday\nSunday\nRegular Schedule\nGreen Rain (Year 1)\nSummer 6 and 16\

In [112]:
RAG("How to raise friendship with Abigail?", top_k=3)

('Short answer: talk to her every day (+20), give her gifts she loves (best), do her delivery requests, trigger heart events with the right dialogue choices, invite her to the movie / buy a snack, and avoid giving things she dislikes or hates.\n\nDetails and practical tips\n\n1) Daily interaction\n- Talk to Abigail once per day for +20 friendship. Don’t skip days (decay applies if you don’t talk).\n\n2) Gifts (the fastest, most reliable method)\n- You can give 1 gift per day and up to 2 gifts per villager per week (the week is Sunday→Saturday). If you give two gifts in the same week you get an extra +10 on Sunday.\n- Birthday (Fall 13): gifts are ×8 — huge boost (use a loved item on her birthday).\n- Stardrop Tea: grants 250 friendship (1 heart) and is NOT subject to the weekly gift limit — a very powerful gift.\n- Loved items for Abigail (give these whenever possible):\n  - Amethyst\n  - Magic Rock Candy\n  - Monster Compendium\n  - Stardrop Tea (special case, see above)\n  - Pufferfi